In [1]:
from csv import DictReader, DictWriter
import json
import requests
import pandas as pd

In [3]:
with open ('vehicle-fuel-type-count-by-zip-code-20231.csv') as file:
    csv_reader = DictReader(file)
    data = list(csv_reader)
#for item in data[:5]:
    #print(item)
with open('output_data.json', 'w') as json_file:
    json.dump(data, json_file, indent=4);

In [4]:
with open('output_data.json', 'r') as json_file:
    data = json.load(json_file)
    zip_codes=[]
for item in data:
    zip_code = item.get('ZIP Code')
    if zip_code.isdigit():
        zip_codes.append(zip_code)
print(zip_codes[:10])
unique_zip_codes = list(set(zip_codes))
print(unique_zip_codes)
        

['91302', '93631', '90603', '93561', '94505', '90606', '92026', '90275', '90024', '92037']
['94545', '97216', '92525', '92807', '93306', '93238', '95021', '90060', '92134', '92689', '96757', '95511', '98572', '99577', '93497', '97730', '93262', '91370', '93387', '92104', '92596', '95641', '94978', '92705', '94601', '91117', '97412', '98062', '92676', '94337', '90277', '95833', '92407', '92452', '94153', '94671', '93549', '99224', '94035', '95958', '96517', '99669', '96634', '99705', '92715', '91754', '93311', '98530', '96078', '91319', '94646', '94606', '99521', '95592', '96050', '93720', '93724', '93303', '93291', '91786', '92220', '96785', '95980', '91205', '91841', '95369', '94807', '97292', '93402', '94563', '95114', '95931', '90560', '97147', '96266', '93003', '97122', '94947', '95200', '92579', '95768', '91830', '95538', '98625', '98208', '90630', '90055', '95353', '97202', '92610', '95765', '95449', '93517', '91081', '95474', '95093', '98601', '90583', '92241', '93565', '99320',

In [7]:
len(unique_zip_codes)

4781

In [9]:
import requests

def get_lat_lon(zip_code):
    url = f"https://geocode.xyz/{zip_code}?json=1"
    
    try:
        response = requests.get(url)
        
        # Check if the response is successful (status code 200)
        if response.status_code == 200:
            data = response.json()
            
            # Check if the response contains latitude and longitude
            if 'latt' in data and 'longt' in data:
                lat = data['latt']
                lon = data['longt']
                
                # Return latitude and longitude if both are found
                return lat, lon
            else:
                print(f"Latitude or Longitude not found for ZIP code {zip_code}")
                return None, None
        else:
            print(f"Error: Received status code {response.status_code} for ZIP code {zip_code}")
            return None, None
            
    except requests.exceptions.RequestException as e:
        print(f"Error fetching data for ZIP code {zip_code}: {e}")
        return None, None

In [11]:
# Loop through ZIP Codes and Fetch Data
lat_lon_data = []
for zip_code in unique_zip_codes:
    lat, lon = get_lat_lon(zip_code)
    lat_lon_data.append({'zip_code': zip_code, 'lat': lat, 'lon': lon})


lat_lon_dict = {lat_lon['zip_code']: (lat_lon['lat'], lat_lon['lon']) for lat_lon in lat_lon_data}

# write the lat lon info into the csv file
rows = []
with open('vehicle-fuel-type-count-by-zip-code-20231.csv', 'r') as file:
    csv_reader = DictReader(file)
    headers = csv_reader.fieldnames
    headers.extend(['lat', 'lon'])

    for row in csv_reader:
        zip_code = row['ZIP Code']
        if zip_code in lat_lon_dict:
            lat, lon = lat_lon_dict[zip_code]
            row['lat'] = lat
            row['lon'] = lon
        rows.append(row)
        

with open('vehicle-fuel-type-count-by-zip-code-20231.csv', 'w') as file:
    csv_writer = DictWriter(file, fieldnames=headers)
    csv_writer.writeheader()
    csv_writer.writerows(rows)

print("CSV file updated successfully with lat and lon information.")  

Latitude or Longitude not found for ZIP code 96634
Latitude or Longitude not found for ZIP code 91319
Latitude or Longitude not found for ZIP code 95768
Latitude or Longitude not found for ZIP code 91081
Latitude or Longitude not found for ZIP code 95908
Latitude or Longitude not found for ZIP code 90799
Latitude or Longitude not found for ZIP code 96838
Latitude or Longitude not found for ZIP code 96662
Latitude or Longitude not found for ZIP code 93941
Latitude or Longitude not found for ZIP code 92471
Latitude or Longitude not found for ZIP code 92788
Latitude or Longitude not found for ZIP code 95744
Latitude or Longitude not found for ZIP code 94842
Latitude or Longitude not found for ZIP code 91988
Latitude or Longitude not found for ZIP code 90675
Latitude or Longitude not found for ZIP code 91774
Error fetching data for ZIP code 97148: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None))
Latitud

In [23]:
df = pd.read_csv('vehicle-fuel-type-count-by-zip-code-20231.csv')

In [25]:
df.tail()

Date ZIP Code Model Year       Fuel       Make   Duty  Vehicles  \
999241  12/31/2023    95206       2017  Flex-Fuel       JEEP  Light      12.0   
999242         NaN      NaN        NaN        NaN        NaN    NaN       NaN   
999243  12/31/2023    98372       2013   Gasoline  OTHER/UNK  Light       1.0   
999244         NaN      NaN        NaN        NaN        NaN    NaN       NaN   
999245  12/31/2023    91789       2022        Unk  OTHER/UNK    Unk       1.0   

             lat         lon  
999241  55.66898    21.19994  
999242       NaN         NaN  
999243   1.24669    103.8428  
999244       NaN         NaN  
999245  34.02068  -117.85921

In [27]:
df.rename(columns={'Date':'date', 'ZIP Code': 'zip_code', 'Model Year': 'model_year', 'Fuel': 'fuel', 'Make': 'make', 'Duty': 'duty', 'Vehicles': 'vehicles', 'lat': 'lat', 'lon': 'lon' }, inplace=True)
df.head()

date zip_code model_year fuel       make duty  vehicles       lat  \
0         NaN      NaN        NaN  NaN        NaN  NaN       NaN       NaN   
1  12/31/2023    91302      <2010  Unk  OTHER/UNK  Unk     490.0  34.13836   
2         NaN      NaN        NaN  NaN        NaN  NaN       NaN       NaN   
3  12/31/2023    93631      <2010  Unk  OTHER/UNK  Unk     414.0   36.5091   
4         NaN      NaN        NaN  NaN        NaN  NaN       NaN       NaN   

          lon  
0         NaN  
1  -118.66129  
2         NaN  
3  -119.54626  
4         NaN

In [29]:
df = df.dropna()
df.head()

date zip_code model_year fuel       make duty  vehicles       lat  \
1  12/31/2023    91302      <2010  Unk  OTHER/UNK  Unk     490.0  34.13836   
3  12/31/2023    93631      <2010  Unk  OTHER/UNK  Unk     414.0   36.5091   
5  12/31/2023    90603      <2010  Unk  OTHER/UNK  Unk     504.0  48.70533   
7  12/31/2023    93561      <2010  Unk  OTHER/UNK  Unk     778.0  48.00511   
9  12/31/2023    94505      <2010  Unk  OTHER/UNK  Unk     387.0  47.76015   

          lon  
1  -118.66129  
3  -119.54626  
5    17.28243  
7    18.65843  
9    18.12112

In [49]:
#Remove all rows from dataframe that have value 'Unk', 'OTHER/UNK' & 'UNKNOWN'
df_cleaned = df[
    (df['model_year'] != 'Unk') & 
    (df['fuel'] != 'Unk') & 
    (df['make'] != 'OTHER/UNK') & 
    (df['make'] != 'UNKNOWN') & 
    (df['duty'] != 'Unk') &
    (df['zip_code'] != 'OOS') &
    (df['lat'] != '0') &
    (df['lon'] != '0') &
    (df['lat'] != 'Throttled! See geocode.xyz/pricing') &
    (df['lon'] != 'Throttled! See geocode.xyz/pricing')
]

In [51]:
len(df_cleaned)

244700

In [53]:
#code example for cleaning column model_year
df_cleaned.loc[:, 'model_year'] = df_cleaned['model_year'].apply(lambda x: 2009 if isinstance(x, str) and x.startswith('<2010') else int(x))

In [55]:
df_cleaned.to_csv('vehicle_cleaned.csv', index=False)

# Uncomment below code & run pip install psycopg2


In [50]:
#pip install psycopg2

   ---------------------------------------- 0.0/1.2 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.2 MB ? eta -:--:--
    --------------------------------------- 0.0/1.2 MB 162.5 kB/s eta 0:00:08
   - -------------------------------------- 0.0/1.2 MB 279.3 kB/s eta 0:00:05
   -- ------------------------------------- 0.1/1.2 MB 435.7 kB/s eta 0:00:03
   --------- ------------------------------ 0.3/1.2 MB 1.4 MB/s eta 0:00:01
   ------------------------- -------------- 0.7/1.2 MB 2.9 MB/s eta 0:00:01
   ---------------------------------------  1.2/1.2 MB 4.3 MB/s eta 0:00:01
   ---------------------------------------- 1.2/1.2 MB 3.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [67]:
# Import the dependencies
import requests
import psycopg2

from sqlalchemy import create_engine, Column, String, Float, Integer, Date
from sqlalchemy.orm import Session
from sqlalchemy.orm import declarative_base

# Create Database 'Vehicle' in Postgresql prior to running below code. 
# In the create_engine step input the correct username:password

In [69]:
# Create a base class for declaring class definitions to produce Table objects
Base = declarative_base()

In [71]:
class Vehicle(Base):
    __tablename__ = 'Vehicle'

    id = Column(Integer, primary_key=True)
    date = Column(Date)
    zip_code = Column(Integer)
    model_year = Column(Integer)
    fuel = Column(String)
    make = Column(String)
    duty = Column(String(50))
    vehicles = Column(Integer)
    lat = Column(Float)
    lon = Column(Float)
    

In [73]:
# Create database engine
engine = create_engine('postgresql://postgres:<password>s@localhost:5432/Vehicle')

# Create the table
Base.metadata.create_all(engine)


session = Session(bind=engine)

In [77]:
# Add data from CSV to the session
for row in df_cleaned.itertuples():
    vehicle_data = Vehicle(
        date=row.date,
        zip_code=row.zip_code,
        model_year=row.model_year,
        fuel=row.fuel,
        make=row.make,
        duty=row.duty,
        vehicles=row.vehicles,
        lat=row.lat,
        lon=row.lon
    )
    session.add(vehicle_data)

# Commit the transaction
session.commit()



In [81]:
data = session.query(Vehicle)
for item in data:
    print(item.zip_code, item.model_year, item.lat, item.lon)

90660 2016 33.98809 -118.08921
94303 2016 47.78397 18.70168
94547 2016 38.00807 -122.26467
93725 2016 36.67955 -119.73938
92505 2016 48.10457 17.68756
95632 2016 48.62151 18.24913
94513 2017 37.92984 -121.71059
95337 2017 37.7779 -121.22842
95336 2017 37.81332 -121.21616
91343 2018 34.23924 -118.48156
95307 2019 37.58453 -120.95074
92346 2020 55.75778 21.15871
92620 2016 33.71132 -117.76267
94403 2017 37.53746 -122.30208
92105 2017 55.71782 21.15284
94560 2016 37.53578 -122.03218
92683 2018 33.75179 -117.9938
95337 2016 37.7779 -121.22842
91770 2019 34.06622 -118.08423
95678 2018 55.92704 23.32416
91766 2018 34.04184 -117.75801
91405 2019 34.20018 -118.44725
91342 2022 22.56214 120.48682
92805 2016 33.83341 -117.90708
92064 2016 48.38953 17.87319
93010 2016 47.93471 17.71168
94565 2019 38.01284 -121.90375
92346 2018 55.75778 21.15871
92114 2020 55.71204 21.13372
92336 2020 55.77461 21.14991
90723 2016 33.89758 -118.16325
93637 2016 36.94623 -120.09415
90660 2021 33.98809 -118.08921
928

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



90603 2016 48.70533 17.28243
90402 2016 34.03575 -118.50301
94585 2016 38.24511 -122.00421
95066 2017 37.06211 -122.01544
91506 2017 34.17198 -118.32451
90715 2017 33.84026 -118.07805
92262 2009 55.72286 21.116
95046 2009 37.0894 -121.59957
95035 2013 37.4345 -121.89426
95037 2014 37.12913 -121.65102
94602 2014 47.82006 17.98452
91709 2014 33.97177 -117.72426
94606 2014 37.82177 -122.25719
92024 2014 -9.52987 -77.52641
94502 2014 37.73799 -122.24512
95065 2010 37.01596 -121.98531
91024 2010 34.16612 -118.05126
93619 2014 36.84638 -119.6571
91307 2012 48.83612 17.83771
90221 2013 33.89434 -118.20447
90210 2014 25.41068 66.6622
92551 2009 48.28287 17.75753
92114 2012 55.71204 21.13372
95841 2009 48.59802 18.43198
95210 2015 38.02513 -121.29826
94122 2016 47.98357 17.99583
94122 2017 47.98357 17.99583
92139 2019 55.71342 21.13661
94030 2019 37.6011 -122.40175
91724 2021 34.08771 -117.85785
90034 2009 1.27352 103.82248
92110 2009 32.76616 -117.20073
94132 2009 48.00912 18.35161
92026 2011 

In [83]:
# Close the session
session.close()